In [51]:
import pandas as pd
import re
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from pymorphy3 import MorphAnalyzer
from nltk.corpus import stopwords
import numpy as np
import torch.nn as nn
from sklearn.model_selection import train_test_split
import torch

In [21]:
stopwords = stopwords.words('russian')

In [22]:
df = pd.read_csv('./data/Petitions.csv')
df

id                               public_petition_text  \
0      3168490                                     снег на дороге   
1      3219678                очистить кабельный киоск от рекламы   
2      2963920  Просим убрать все деревья и кустарники, которы...   
3      3374910  Неудовлетворительное состояние парадной - надп...   
4      3336285                                           Граффити   
...        ...                                                ...   
59884  3128111                           прошу закрасить граффити   
59885  3276713       Прошу вас отремонтировать пешеходную дорожку   
59886  3274663  Необходимо демонтировать незаконную рекламную ...   
59887  3359308  Очень гремит на ветру металлическая часть окна...   
59888  3209098  Две проблемы в одном:\n1) Незаконные надписи/о...   

                                         reason_category  
0                                        Благоустройство  
1                                        Благоустройство  
2                                        Благоустройство  
3                                         Содержание МКД  
4                                        Благоустройство  
...                                                  ...  
59884                                    Благоустройство  
59885                                    Благоустройство  
59886  Незаконная информационная и (или) рекламная ко...  
59887                                             Кровля  
59888                                    Благоустройство  

[59889 rows x 3 columns]

In [23]:
print(len(df['reason_category'].unique()), "\n", df['reason_category'].value_counts())

15 
 reason_category
Благоустройство                                                                     34769
Содержание МКД                                                                      14461
Нарушение правил пользования общим имуществом                                        2170
Незаконная информационная и (или) рекламная конструкция                              1831
Фасад                                                                                1483
Повреждения или неисправность элементов уличной инфраструктуры                       1164
Кровля                                                                                825
Водоснабжение                                                                         809
Состояние рекламных или информационных конструкций                                    673
Санитарное состояние                                                                  434
Центральное отопление                                                          

In [24]:
df.drop(columns="id", inplace=True)

In [25]:
new_df = df.sample(100)
new_df

public_petition_text  \
7054   Во дворе дома, под аркой свален крупногабаритн...   
51545                              Яма на проезжей части   
44811  Развалился светильник над входной дверью в пар...   
11247                                           очистите   
56799  В подъездах дома установлены конструкции для п...   
...                                                  ...   
42387                                             листва   
40612  К заявке 2965322. В заявке было требование убр...   
6022   Здравствуйте. Прошу рассмотреть возможность ус...   
14875  Вблизи остановки общественного транспорта "Про...   
35254     Шины на газоне у дома 17/13 по улице Оборонная   

                                      reason_category  
7054                                  Благоустройство  
51545                                 Благоустройство  
44811                                  Содержание МКД  
11247                                  Содержание МКД  
56799  Нарушение порядка пользования общим имуществом  
...                                               ...  
42387                                 Благоустройство  
40612                                 Благоустройство  
6022                                  Благоустройство  
14875                                 Благоустройство  
35254                                 Благоустройство  

[100 rows x 2 columns]

In [26]:
X = new_df["public_petition_text"].to_list()
y = new_df["reason_category"].to_list()

In [27]:
text1 = ['<p> Привет, чурка! Также Я: любл%ю тебя; и был @$, но не ты дурак</p>', 'Привет, чурка, я в Дубае']

In [28]:
# html_tag=re.compile('<.*?>')
# text = html_tag.sub('', text)
# text

In [29]:
def preprocessing_text(text):
    lst = []
    #remove html
    for i in text:
        html_tag=re.compile('<.*?>')
        text_no_html = html_tag.sub('', i)
        #remove quots
        text_only_letters = re.sub('[^\w\s]', '', text_no_html)
        #tokenizим
        words = word_tokenize(text_only_letters)
        #morphим
        morph = MorphAnalyzer()
        lemmas = [morph.normal_forms(w)[0] for w in words]
        #del_sw
        prepared = [w for w in lemmas if w not in stopwords]
        lemm_sentce = ' '.join(prepared)
        lst.append(lemm_sentce)
        # lst.append(prepared)
    return lst


In [30]:
prepro_text = preprocessing_text(text=X)
prepro_text

['двор дом арка свальный крупногабаритный мусор большой количество картонный коробка xxxxxxxxxxxxx xxxxxx xxxxxxxxxx x xxxxxxxxxxxxx xxxxxxxxxxx сегодняшний день 03042021 мусор убрать количество увеличиться проблема устранить',
 'яма проезжий часть',
 'развалиться светильник входной дверь парадный 3 несколько обращаться просьба заменить новый установить соседний парадное второй четвёртый ответ просьба произвести замена лампа светильник который долго хватать качество освещение ниже положить гост',
 'очистить',
 'подъезд дом установить конструкция показ реклама согласие собственник',
 'незаконный вывескарекламный конструкция адрес санктпетербург митрофаньевский широта далее 29 бежать строкасветовый табло',
 'здравствуйте xxxxx xxxxx xxxxxxxx xxxxxxx xxxxxxxxx библиотека месалтыковащедрин находиться адрес богатырский проспект д9 штатный единица дворник снег крыльцаа дом находиться библиотека приходиться уборщицамтк трактор проезжать показать ниже фото дворник который производить уборка до

In [283]:
count_vocab = set((' '.join(prepro_text).split()))
word_to_ix = {word: i for i, word in enumerate(count_vocab)}

In [302]:
word_list = list(word_to_ix.keys())
word_list

['кругом',
 'подстанция',
 '23',
 'изпод',
 'проходимость',
 'образоваться',
 'разрешать',
 'xxxxxxxxxxxxx',
 'забитый',
 'открыть',
 'ремонт',
 'куст',
 'утро',
 'больший',
 'мыть',
 'дать',
 'систематически',
 'иметь',
 'связь',
 'левый',
 'цокольный',
 'желательно',
 'день',
 'земля',
 'большой',
 'сегодняшний',
 'устранить',
 'вблизи',
 '3101',
 'эвакуация',
 'хотеться',
 'щит',
 'единственный',
 'ям',
 'сообщение',
 'работа',
 'поворот',
 '6111',
 'заявка',
 'мусор',
 'д9',
 '293',
 'отклонить',
 'загромождать',
 'листва',
 'территория',
 'весельный',
 'цвет',
 'картонный',
 'требоваться',
 'фаза',
 'нужда',
 'снег',
 'урна',
 'висеть',
 'обмотка',
 'балкон',
 'красота',
 'яма',
 'который',
 'рф',
 '29',
 'xxxxxxx',
 'грунт',
 'площадь',
 'двор',
 'проваливаться',
 'согласие',
 'зачистить',
 'торец',
 'кататься',
 'бутылка',
 'дверь',
 'столб',
 'апрель',
 'дорога',
 'определить',
 'произвести',
 '6м',
 'проверить',
 'средство',
 'парадное',
 'белорусский',
 'неделя',
 'ворота',
 

In [305]:
with open('word_list3.tsv', 'w', encoding='utf-8') as f:
    f.write('\n'.join(word_list))

In [131]:
dframe = pd.DataFrame(prepro_text, columns=['X'])
dframe

X
0   двор дом арка свальный крупногабаритный мусор ...
1                                  яма проезжий часть
2   развалиться светильник входной дверь парадный ...
3                                            очистить
4   подъезд дом установить конструкция показ рекла...
..                                                ...
95                                             листва
96  заявка 2965322 заявка требование убрать листва...
97  здравствуйте просить рассмотреть возможность у...
98  вблизи остановка общественный транспорт проспе...
99                шина газон дом 1713 улица оборонный

[100 rows x 1 columns]

In [132]:
dframe['Y'] = y

In [133]:
dframe

X  \
0   двор дом арка свальный крупногабаритный мусор ...   
1                                  яма проезжий часть   
2   развалиться светильник входной дверь парадный ...   
3                                            очистить   
4   подъезд дом установить конструкция показ рекла...   
..                                                ...   
95                                             листва   
96  заявка 2965322 заявка требование убрать листва...   
97  здравствуйте просить рассмотреть возможность у...   
98  вблизи остановка общественный транспорт проспе...   
99                шина газон дом 1713 улица оборонный   

                                                 Y  
0                                  Благоустройство  
1                                  Благоустройство  
2                                   Содержание МКД  
3                                   Содержание МКД  
4   Нарушение порядка пользования общим имуществом  
..                                             ...  
95                                 Благоустройство  
96                                 Благоустройство  
97                                 Благоустройство  
98                                 Благоустройство  
99                                 Благоустройство  

[100 rows x 2 columns]

In [38]:
def embedding_matrix(f):
    count_vocab = set((' '.join(f).split()))
    print(len(count_vocab))
    word_to_ix = {word: i for i, word in enumerate(count_vocab)}
    print(word_to_ix)
    a = max(word_to_ix.values()) + 1
    print(a)
    matrica = [[0] * a for _ in range(a)]
    for k in range(0, len(f)):
        b = len(f[k].split())
        words = f[k].split()
        for i in range(b):
            for j in range(i+1, b):
                if words[i] in f[k] and words[j] in f[k]:
                    matrica[word_to_ix[words[i]]][word_to_ix[words[j]]] += 1
                    matrica[word_to_ix[words[j]]][word_to_ix[words[i]]] += 1

    # for row in matrica:
    #     print(row)
    
    return matrica

In [39]:
emb_matr = embedding_matrix(prepro_text)
emb_matr

692
{'кругом': 0, 'подстанция': 1, '23': 2, 'изпод': 3, 'проходимость': 4, 'образоваться': 5, 'разрешать': 6, 'xxxxxxxxxxxxx': 7, 'забитый': 8, 'открыть': 9, 'ремонт': 10, 'куст': 11, 'утро': 12, 'больший': 13, 'мыть': 14, 'дать': 15, 'систематически': 16, 'иметь': 17, 'связь': 18, 'левый': 19, 'цокольный': 20, 'желательно': 21, 'день': 22, 'земля': 23, 'большой': 24, 'сегодняшний': 25, 'устранить': 26, 'вблизи': 27, '3101': 28, 'эвакуация': 29, 'хотеться': 30, 'щит': 31, 'единственный': 32, 'ям': 33, 'сообщение': 34, 'работа': 35, 'поворот': 36, '6111': 37, 'заявка': 38, 'мусор': 39, 'д9': 40, '293': 41, 'отклонить': 42, 'загромождать': 43, 'листва': 44, 'территория': 45, 'весельный': 46, 'цвет': 47, 'картонный': 48, 'требоваться': 49, 'фаза': 50, 'нужда': 51, 'снег': 52, 'урна': 53, 'висеть': 54, 'обмотка': 55, 'балкон': 56, 'красота': 57, 'яма': 58, 'который': 59, 'рф': 60, '29': 61, 'xxxxxxx': 62, 'грунт': 63, 'площадь': 64, 'двор': 65, 'проваливаться': 66, 'согласие': 67, 'зачисти

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  1,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [40]:
from sklearn.decomposition import PCA

In [45]:
pca = PCA(n_components=30)
pca.fit(emb_matr)
data_pca = pca.transform(emb_matr)

In [47]:
np.savetxt('embeddings.tsv', data_pca, delimiter='\t')

## Neural_buri

In [48]:
count_vocab2 = set((' '.join(prepro_text).split()))
print(len(count_vocab2))
word_to_ix2 = {word: i for i, word in enumerate(count_vocab2)}
word_to_ix2

692


{'кругом': 0,
 'подстанция': 1,
 '23': 2,
 'изпод': 3,
 'проходимость': 4,
 'образоваться': 5,
 'разрешать': 6,
 'xxxxxxxxxxxxx': 7,
 'забитый': 8,
 'открыть': 9,
 'ремонт': 10,
 'куст': 11,
 'утро': 12,
 'больший': 13,
 'мыть': 14,
 'дать': 15,
 'систематически': 16,
 'иметь': 17,
 'связь': 18,
 'левый': 19,
 'цокольный': 20,
 'желательно': 21,
 'день': 22,
 'земля': 23,
 'большой': 24,
 'сегодняшний': 25,
 'устранить': 26,
 'вблизи': 27,
 '3101': 28,
 'эвакуация': 29,
 'хотеться': 30,
 'щит': 31,
 'единственный': 32,
 'ям': 33,
 'сообщение': 34,
 'работа': 35,
 'поворот': 36,
 '6111': 37,
 'заявка': 38,
 'мусор': 39,
 'д9': 40,
 '293': 41,
 'отклонить': 42,
 'загромождать': 43,
 'листва': 44,
 'территория': 45,
 'весельный': 46,
 'цвет': 47,
 'картонный': 48,
 'требоваться': 49,
 'фаза': 50,
 'нужда': 51,
 'снег': 52,
 'урна': 53,
 'висеть': 54,
 'обмотка': 55,
 'балкон': 56,
 'красота': 57,
 'яма': 58,
 'который': 59,
 'рф': 60,
 '29': 61,
 'xxxxxxx': 62,
 'грунт': 63,
 'площадь': 6

In [49]:
lookup = {value: key for key, value in word_to_ix2.items()}
lookup

{0: 'кругом',
 1: 'подстанция',
 2: '23',
 3: 'изпод',
 4: 'проходимость',
 5: 'образоваться',
 6: 'разрешать',
 7: 'xxxxxxxxxxxxx',
 8: 'забитый',
 9: 'открыть',
 10: 'ремонт',
 11: 'куст',
 12: 'утро',
 13: 'больший',
 14: 'мыть',
 15: 'дать',
 16: 'систематически',
 17: 'иметь',
 18: 'связь',
 19: 'левый',
 20: 'цокольный',
 21: 'желательно',
 22: 'день',
 23: 'земля',
 24: 'большой',
 25: 'сегодняшний',
 26: 'устранить',
 27: 'вблизи',
 28: '3101',
 29: 'эвакуация',
 30: 'хотеться',
 31: 'щит',
 32: 'единственный',
 33: 'ям',
 34: 'сообщение',
 35: 'работа',
 36: 'поворот',
 37: '6111',
 38: 'заявка',
 39: 'мусор',
 40: 'д9',
 41: '293',
 42: 'отклонить',
 43: 'загромождать',
 44: 'листва',
 45: 'территория',
 46: 'весельный',
 47: 'цвет',
 48: 'картонный',
 49: 'требоваться',
 50: 'фаза',
 51: 'нужда',
 52: 'снег',
 53: 'урна',
 54: 'висеть',
 55: 'обмотка',
 56: 'балкон',
 57: 'красота',
 58: 'яма',
 59: 'который',
 60: 'рф',
 61: '29',
 62: 'xxxxxxx',
 63: 'грунт',
 64: 'площадь

In [118]:
num_emb = list(lookup.keys())
len(num_emb)

692

In [99]:
embs = nn.Embedding(len(num_emb), 3)
input = torch.tensor(num_emb)

In [139]:
import torch.nn.functional as F

In [314]:
class CBOWModeler(nn.Module):

    def __init__(self, vocab_size, embedding_dim, context_size):
        super(CBOWModeler, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.linear1 = nn.Linear(context_size * embedding_dim, 250)
        self.linear2 = nn.Linear(250, vocab_size)

    def forward(self, inputs):
        embeds = self.embeddings(inputs).view((1, -1))
        out1 = F.relu(self.linear1(embeds))
        out2 = self.linear2(out1)           
        #print(embeds)
        log_probs = F.log_softmax(out2, dim=1)
        return log_probs

    def predict(self,input):
        context_idxs = torch.tensor([word_to_ix2[w] for w in input], dtype=torch.long)
        res = self.forward(context_idxs)
        res_arg = torch.argmax(res)
        res_val, res_ind = res.sort(descending=True)
        res_val = res_val[0][:1]
        res_ind = res_ind[0][:1]
        #print(res_val)
        #print(res_ind)
        for arg in zip(res_val,res_ind):
            #print(arg)
            print([(key,val,arg[0]) for key,val in word_to_ix2.items() if val == arg[1]])

In [315]:
loss_function = nn.NLLLoss()

In [316]:
model = CBOWModeler(len(num_emb), 10, 3)

In [201]:
optimizer = torch.optim.SGD(model.parameters(), lr=0.001)

In [317]:
model.predict(['двор', 'арка', 'лист'])
# двор дом арка свальный

[('единица', 576, tensor(-5.5987, grad_fn=<UnbindBackward0>))]


In [227]:
wordvecs = model.linear2.weight.cpu().detach().numpy()
wordvecs

array([[ 0.0251831 , -0.02891936, -0.03031075, ...,  0.03528842,
        -0.03260382,  0.03102396],
       [ 0.05762857, -0.05076442, -0.04819339, ..., -0.00330954,
         0.05132478,  0.017945  ],
       [ 0.04069733, -0.01938121, -0.05274904, ...,  0.02470092,
        -0.04803883,  0.04907109],
       ...,
       [-0.0528859 , -0.01634015,  0.03947989, ..., -0.01430494,
         0.04670191,  0.0130012 ],
       [-0.05101476, -0.01645047, -0.01007505, ...,  0.00647969,
         0.01355693,  0.00826564],
       [ 0.00495719,  0.05280975, -0.0389386 , ...,  0.03492624,
         0.00658961,  0.03668834]], dtype=float32)

In [228]:
np.savetxt('word2vec_vectors.tsv', wordvecs, delimiter='\t')

In [205]:
dframe['X'][0].split()

['двор',
 'дом',
 'арка',
 'свальный',
 'крупногабаритный',
 'мусор',
 'большой',
 'количество',
 'картонный',
 'коробка',
 'xxxxxxxxxxxxx',
 'xxxxxx',
 'xxxxxxxxxx',
 'x',
 'xxxxxxxxxxxxx',
 'xxxxxxxxxxx',
 'сегодняшний',
 'день',
 '03042021',
 'мусор',
 'убрать',
 'количество',
 'увеличиться',
 'проблема',
 'устранить']

In [ ]:
epochs = 5

loss_values = []
for epoch in range(epochs):
    for x_b, y_b in train_dl:

        outputs = model(x_b)

        loss_value = loss_function(outputs, y_b)

        loss_value.backward()

        optimizer.step()

        optimizer.zero_grad()
    loss_values.append(loss_value.item())

    print(f'Эпоха {epoch + 1}, Значение функции потерь: {loss_value.item()}')